In [1]:
!python -m pip install html2text

In [2]:
!python -m pip install mistletoe

In [3]:
%load_ext autoreload
%autoreload 2

In [4]:
from contextlib import closing
from html2text import HTML2Text
from bs4 import BeautifulSoup
from pathlib import Path
from IPython.display import HTML as HTML_raw, display

import json
import sys
import re
import logging
import pandas as pd
import requests
import warcio
import mistletoe

# https://github.com/miyuchina/mistletoe

In [5]:
websites = pd.read_csv("./ccmain/ccmain_2021-04_Long2.txt", header = None, sep = '|') 

In [6]:
websites.head()

0                                                  1  \
0 NaN  https://globalannal.wordpress.com/tag/careers/...   
1 NaN  https://globalannal.wordpress.com/tag/jobs-num...   
2 NaN  https://globalannal.wordpress.com/tag/jobs-rep...   
3 NaN  https://globalshapersbucharest.wordpress.com/2...   
4 NaN  https://globalyouthbook.wordpress.com/tag/care...   

                                                   2   3  
0  crawl-data/CC-MAIN-2021-04/segments/1610703528... NaN  
1  crawl-data/CC-MAIN-2021-04/segments/1610703528... NaN  
2  crawl-data/CC-MAIN-2021-04/segments/1610703528... NaN  
3  crawl-data/CC-MAIN-2021-04/segments/1610703506... NaN  
4  crawl-data/CC-MAIN-2021-04/segments/1610704798... NaN

In [7]:
websites.columns

Int64Index([0, 1, 2, 3], dtype='int64')

In [8]:
websites.drop([0, 3], axis=1, inplace=True)
websites.head()

1  \
0  https://globalannal.wordpress.com/tag/careers/...   
1  https://globalannal.wordpress.com/tag/jobs-num...   
2  https://globalannal.wordpress.com/tag/jobs-rep...   
3  https://globalshapersbucharest.wordpress.com/2...   
4  https://globalyouthbook.wordpress.com/tag/care...   

                                                   2  
0  crawl-data/CC-MAIN-2021-04/segments/1610703528...  
1  crawl-data/CC-MAIN-2021-04/segments/1610703528...  
2  crawl-data/CC-MAIN-2021-04/segments/1610703528...  
3  crawl-data/CC-MAIN-2021-04/segments/1610703506...  
4  crawl-data/CC-MAIN-2021-04/segments/1610704798...

In [9]:
websites.columns = ['url_link', 'warc_file']
websites.head()

url_link  \
0  https://globalannal.wordpress.com/tag/careers/...   
1  https://globalannal.wordpress.com/tag/jobs-num...   
2  https://globalannal.wordpress.com/tag/jobs-rep...   
3  https://globalshapersbucharest.wordpress.com/2...   
4  https://globalyouthbook.wordpress.com/tag/care...   

                                           warc_file  
0  crawl-data/CC-MAIN-2021-04/segments/1610703528...  
1  crawl-data/CC-MAIN-2021-04/segments/1610703528...  
2  crawl-data/CC-MAIN-2021-04/segments/1610703528...  
3  crawl-data/CC-MAIN-2021-04/segments/1610703506...  
4  crawl-data/CC-MAIN-2021-04/segments/1610704798...

In [10]:
websites.url_link.value_counts()

https://seeker.worksourcewa.com/jobsearch/powersearch.aspx?where=Washington                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      7
https://www.xn--itbaw-ova.de/jobs/151816/werkstudent-w-strich-m-strich-d-fuer-bachelor-master-oder-projektarbeiten-softwareentwicklung-java-in-stuttgart-und-karlsruhe                                                               

In [11]:
websites.url_link.value_counts().keys()

Index(['https://seeker.worksourcewa.com/jobsearch/powersearch.aspx?where=Washington                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  ',
       'https://www.xn--itbaw-ova.de/jobs/151816/werkstudent-w-strich-m-strich-d-fuer-bachelor-master-oder-projektarbeiten-softwareentwicklung-java-in-stuttgart-und-karlsruhe                                                  

In [12]:
urlList = []
for i in websites.url_link.value_counts().keys():
    urlList.append(i.replace(' ',''))
    
print(urlList[:20])

['https://seeker.worksourcewa.com/jobsearch/powersearch.aspx?where=Washington', 'https://www.xn--itbaw-ova.de/jobs/151816/werkstudent-w-strich-m-strich-d-fuer-bachelor-master-oder-projektarbeiten-softwareentwicklung-java-in-stuttgart-und-karlsruhe', 'https://www.xn--itbaw-ova.de/jobs/151789/werkstudent-w-strich-m-strich-d-softwareentwicklung-java-in-stuttgart-und-karlsruhe', 'https://www.xn--itbaw-ova.de/jobs/152230/senior-software-engineer-w-strich-m-strich-d-sap-in-stuttgart-karlsruhe-und-reutlingen', 'https://help.workable.com/hc/en-us/articles/115012441868-Which-job-boards-can-I-post-to-through-Workable-', 'https://www.xn--itbaw-ova.de/jobs/151969/senior-software-engineer-w-strich-m-strich-d-java-in-stuttgart-karlsruhe-und-reutlingen', 'https://www.workitdaily.com/should-quit-job-questions', 'http://www.work521.com/jobs/2452.html', 'https://www.vdk.de/bayern/pages/presse/vdk-zeitung/vdk-zeitung_archiv/80394/minijob_sichert_anspruch', 'https://www.xn--itbaw-ova.de/jobs/152451/softwa

In [13]:
!python -m pip install cdx_toolkit

In [14]:
import cdx_toolkit

In [15]:
cdx = cdx_toolkit.CDXFetcher(source='cc')

In [16]:
cdx_indexes = requests.get('https://index.commoncrawl.org/collinfo.json').json()

In [17]:
pd.options.display.max_colwidth=150
pd.options.display.max_rows=6

In [18]:
pd.DataFrame(cdx_indexes)

id                            name  \
0     CC-MAIN-2021-04              January 2021 Index   
1     CC-MAIN-2020-50             November 2020 Index   
2     CC-MAIN-2020-45              October 2020 Index   
..                ...                             ...   
75       CC-MAIN-2012         Index of 2012 ARC files   
76  CC-MAIN-2009-2010  Index of 2009 - 2010 ARC files   
77  CC-MAIN-2008-2009  Index of 2008 - 2009 ARC files   

                                            timegate  \
0     https://index.commoncrawl.org/CC-MAIN-2021-04/   
1     https://index.commoncrawl.org/CC-MAIN-2020-50/   
2     https://index.commoncrawl.org/CC-MAIN-2020-45/   
..                                               ...   
75       https://index.commoncrawl.org/CC-MAIN-2012/   
76  https://index.commoncrawl.org/CC-MAIN-2009-2010/   
77  https://index.commoncrawl.org/CC-MAIN-2008-2009/   

                                                  cdx-api  
0     https://index.commoncrawl.org/CC-MAIN-2021-04-index  
1     https://index.commoncrawl.org/CC-MAIN-2020-50-index  
2     https://index.commoncrawl.org/CC-MAIN-2020-45-index  
..                                                    ...  
75       https://index.commoncrawl.org/CC-MAIN-2012-index  
76  https://index.commoncrawl.org/CC-MAIN-2009-2010-index  
77  https://index.commoncrawl.org/CC-MAIN-2008-2009-index  

[78 rows x 4 columns]

In [19]:
print(pd.DataFrame(cdx_indexes).head(20).to_markdown())

|    | id              | name                 | timegate                                       | cdx-api                                             |
|---:|:----------------|:---------------------|:-----------------------------------------------|:----------------------------------------------------|
|  0 | CC-MAIN-2021-04 | January 2021 Index   | https://index.commoncrawl.org/CC-MAIN-2021-04/ | https://index.commoncrawl.org/CC-MAIN-2021-04-index |
|  1 | CC-MAIN-2020-50 | November 2020 Index  | https://index.commoncrawl.org/CC-MAIN-2020-50/ | https://index.commoncrawl.org/CC-MAIN-2020-50-index |
|  2 | CC-MAIN-2020-45 | October 2020 Index   | https://index.commoncrawl.org/CC-MAIN-2020-45/ | https://index.commoncrawl.org/CC-MAIN-2020-45-index |
|  3 | CC-MAIN-2020-40 | September 2020 Index | https://index.commoncrawl.org/CC-MAIN-2020-40/ | https://index.commoncrawl.org/CC-MAIN-2020-40-index |
|  4 | CC-MAIN-2020-34 | August 2020 Index    | https://index.commoncrawl.org/CC-MAIN-2020-34/

In [20]:
print(pd.DataFrame(cdx_indexes).tail(20).to_markdown())

|    | id                | name                           | timegate                                         | cdx-api                                               |
|---:|:------------------|:-------------------------------|:-------------------------------------------------|:------------------------------------------------------|
| 58 | CC-MAIN-2015-32   | July 2015 Index                | https://index.commoncrawl.org/CC-MAIN-2015-32/   | https://index.commoncrawl.org/CC-MAIN-2015-32-index   |
| 59 | CC-MAIN-2015-27   | June 2015 Index                | https://index.commoncrawl.org/CC-MAIN-2015-27/   | https://index.commoncrawl.org/CC-MAIN-2015-27-index   |
| 60 | CC-MAIN-2015-22   | May 2015 Index                 | https://index.commoncrawl.org/CC-MAIN-2015-22/   | https://index.commoncrawl.org/CC-MAIN-2015-22-index   |
| 61 | CC-MAIN-2015-18   | April 2015 Index               | https://index.commoncrawl.org/CC-MAIN-2015-18/   | https://index.commoncrawl.org/CC-MAIN-2015-18-index   

In [21]:
api_url = cdx_indexes[0]['cdx-api']
api_url

'https://index.commoncrawl.org/CC-MAIN-2021-04-index'

In [22]:
f = open(r"ccmain_2021jan_jobURL.txt","a+")
for url_link in urlList:
    r = requests.get(api_url,
                 params = {
                     'url': url_link,
                     'output': 'json',
                     'filter': ['=status:200', '=mime-detected:text/html']
                 })
    try:
        records = [json.loads(line) for line in r.text.split('\n') if line]
        df = pd.DataFrame(records)
        print(url_link,' ',df.shape[0])
        L = [str(url_link),' ',str(df.shape[0]), '\n']
        f.writelines(L) 
    except Exception as e:
        print(e)
f.close()

https://seeker.worksourcewa.com/jobsearch/powersearch.aspx?where=Washington   7
https://www.xn--itbaw-ova.de/jobs/151816/werkstudent-w-strich-m-strich-d-fuer-bachelor-master-oder-projektarbeiten-softwareentwicklung-java-in-stuttgart-und-karlsruhe   5
https://www.xn--itbaw-ova.de/jobs/151789/werkstudent-w-strich-m-strich-d-softwareentwicklung-java-in-stuttgart-und-karlsruhe   4
https://www.xn--itbaw-ova.de/jobs/152230/senior-software-engineer-w-strich-m-strich-d-sap-in-stuttgart-karlsruhe-und-reutlingen   4
https://help.workable.com/hc/en-us/articles/115012441868-Which-job-boards-can-I-post-to-through-Workable-   3
https://www.xn--itbaw-ova.de/jobs/151969/senior-software-engineer-w-strich-m-strich-d-java-in-stuttgart-karlsruhe-und-reutlingen   3
https://www.workitdaily.com/should-quit-job-questions   3
http://www.work521.com/jobs/2452.html   1
https://www.vdk.de/bayern/pages/presse/vdk-zeitung/vdk-zeitung_archiv/80394/minijob_sichert_anspruch   1
https://www.xn--itbaw-ova.de/jobs/152451

https://www.vitamindservice.de/faq/welchen-job-k%C3%B6nnte-ich-machen   2
https://www.workselection.com/job/maurer-region-aargau-m-w-d-basel-6558/   2
https://www.workselection.com/job/marketing-und-communication-assistantbaden-6627/   2
https://www.wilkenwerk.de/eventagentur-fuer-live-kommunikation/jobs/   2
https://vancouverwritingjobs.wordpress.com/tag/vancouver-writing-jobs/   2
https://startthinkingright.wordpress.com/2009/11/11/obama-continues-rampant-dishonesty-with-stimulus-jobs/   1
https://resources.workable.com/hr-onboarding-specialist-job-description   2
https://www.xn--itbaw-ova.de/jobs/152468/software-engineer-w-strich-m-strich-d-java-in-stuttgart-karlsruhe-und-reutlingen   2
https://www.xn--itbaw-ova.de/jobs/154805/senior-consultant-w-strich-m-strich-d-sales-und-service-in-stuttgart-und-reutlingen   2
https://resources.workable.com/junior-recruiter-job-description   2
https://www.wirtschaftsjobs.de/finanzbuchhaltung-bilanzbuchhaltung-jobs-stellenangebote   2
https://work

https://www.workitdaily.com/balance-grad-school-full-time-job   2
http://www.work521.com/jobs/37470.html   1
https://www.vgbs.de/jobs-praktika-mehr/jobs   3
https://www.workinsports.com/wisquickregseojob-fr.asp?idx=502025   2
https://workingthoughts.com/2010/01/29/unsurprising-job-survey-results-show-a-ready-to-jump-workforce/   1
https://www.wildigarten.de/2020/07/20/optimal-mobil-jobrad-bei-wildigarten/   2
https://missosmosisteachingresources.wordpress.com/2020/06/15/how-can-we-promote-careers-in-stem-to-girls-in-school/   2
https://www.workinsports.com/wisquickregseojob-fr.asp?idx=502093   2
https://lucas2012infos.wordpress.com/2014/01/10/zerohedge-tyler-durden-its-official-the-us-created-less-jobs-in-2013-than-2012/   2
https://www.workselection.com/job/heizungsmonteur-region-basel-m-w-d-basel-6551/   2
https://www.workitdaily.com/how-to-prepare-job-fair   2
https://www.workselection.com/job/zimmermann-region-baselland-m-w-d-liestal-6660/   2
https://www.workselection.com/job/cnc-

https://www.workselection.com/job/immobiilienbewirtschafter-mit-eidg-fachausweis-m-w-d-olten-6525/   2
https://www.workselection.com/job/process-engineer-cesr-project-m-w-d-rotkreuz-6519/   2
https://www.workselection.com/job/automatiker-m-w-d-luzern-6500/   2
https://www.wp-jobs24.de/job/werksstudent-webentwickler-fuer-wordpress-in-oldenburg-m-w-d-2/   2
https://mlblogsnofavoriteteam.wordpress.com/2014/09/26/derek-jeter-shines-in-final-home-game-of-career/   2
https://www.workselection.com/job/consumables-manager-80-100-m-w-d-rotkreuz-6583/   2
https://tefltravelling.wordpress.com/tag/career/   2
https://help.workable.com/hc/en-us/articles/115012396068-Why-isn-t-my-job-receiving-views-or-candidates-   2
https://www.workitdaily.com/romans-teach-about-career-change   2
https://wirsuchenmenschen.de/azubi-job-matching/results/   2
https://www.wiwo.de/erfolg/trends/zeitdruck-im-job-20-000-blitzentscheidungen-pro-tag/5445178.html   2
http://www.xn--jobs-fr-bayreuth-ozb.de/job/medizinische-f

https://xenagos.de/vertrieb-jobs/account-manager-w-m-d-in-store-marketing/   2
https://www.workselection.com/job/polymechaniker-cnc-drehen-m-w-d-liestal-6686/   2
https://www.wildigarten.de/jobs-villingen-schwenningen/   2
https://www.wuerth.de/web/de/awkg/karriere/jobs/stellensuche/job-finden.php   2
https://www.workselection.com/job/fahrleitungsmonteur-region-s-dostschweiz-m-w-d-basel-6570/   2
https://maghribfoot.wordpress.com/2019/07/07/renard-set-to-resign-from-morocco-job/   2
https://www.workwithglee.com/jobs   3
https://www.workselection.com/job/call-agent-d-f-m-w-d-30-60-dietlikon-6459/   2
https://halifsblog.wordpress.com/2019/10/14/cristiano-ronaldo-scores-700-career-goal/   2
https://www.workselection.com/job/hr-sachbearbeiterin-care-management-spezialistin-m-w-d-80-bis-100-baden-6595/   2
https://www.workselection.com/job/metallbauer-region-baselland-m-w-d-arlesheim-6543/   2
https://www.workselection.com/job/labor-spezialist-m-w-d-zug-6507/   2
https://www.xn--itbaw-ova.d

...

https://wirsuchenphysiotherapeuten.de/jobs/ausbildung-zum-altenpfleger-m-w-d-augustinushaus/   1
Expecting value: line 1 column 1 (char 0)
https://www.workopolis.com/jobsearch/find-jobs?ak=loblaw&l=caledon+village+on&lg=en&pn=4&from=pagination&pp=AFAAAAAAAAAAAAAAAAGUDh_TAQEBEwOo8ONLg89x1uLUU1wZ1S5xs2m58jIfPzAZJH_cWQepZNNyym6jhUNX4b0qqkq0gIw_lw   1
https://www.wir-sind-mint.de/stellenangebote/jobs-im-plz-bereich-1   1
https://functional.works-hub.com/jobs/lead-engineer-2d0   1
https://voelkel-siegen.de/jobs.php   1
https://www.workana.com/es/job/disenador-web-463   1
https://www.workopolis.com/jobsearch/viewjob/lrHDYaIjgnjAh2O7fL6AWEHLyNES6U0WdxMLRjtZ0PmddsMXKKqPpA?ak=&l=Boisbriand%2C+QC   1
https://www.workwide.de/jobs/tauche-ein-in-die-welt-des-online-gamings-und-arbeite-als-kundenservicemitarbeiter/   1
https://www.workana.com/es/job/app-mejor-cotizacion-del-dia   1
Expecting value: line 1 column 1 (char 0)
Expecting value: line 1 column 1 (char 0)
https://patriceayme.wordpress.com/2

Expecting value: line 1 column 1 (char 0)
http://www.work4a.com/search/jobs/485311/Mental-Healthcare-Assistant.html   1
https://ioeteconunthe.wordpress.com/2016/09/03/balsamo-rivitalizzante-burro-di-karite-e-broccoli-neobio-e-balsamo-al-the-verde-e-olio-di-jojoba-eco-cosmetics/?like_comment=1821&_wpnonce=c87f15baf5   1
http://www.work4a.com/search/jobs/483935/Registered-Manager.html   1
Expecting value: line 1 column 1 (char 0)
https://www.workana.com/pt/job/desenvolvimento-de-identidade-visual-12   1
Expecting value: line 1 column 1 (char 0)
http://www.work4a.com/search/jobs/485294/Theatre-Endoscopy-Nurse.html   1
https://www.workana.com/pt/job/pagina-de-captura-37   1
https://vera-via.de/jobs-karriere/stellenmarkt/international/job/2693-sozial-media-berater-m-w-d-fuer-iqos-produkte-in-portugal   1
https://www.workopolis.com/jobsearch/viewjob/QM_XFhovFMW6_WnU6kih8acVqmsrmzaD4tK20SHY2qG0DrMTdkc_yg?ak=bombardier&l=montreal+qc   1
http://world-poker-king.com/yangery/commitment-to-equal-o

https://thecareerguide.wordpress.com/category/ellen-helps-sheri-get-the-job/   1
http://www.xn--jobs-fr-braunschweig-uec.de/job/steuerfachangestellte-m-w-d.517858565.html   1
https://www.workana.com/es/job/seo-a-mi-pagina-web   1
https://www.wfb-gottessegen.de/jobs   1
Expecting value: line 1 column 1 (char 0)
https://www.workana.com/jobs?category=it-programming&page=5   1
https://www.workana.com/pt/job/contrata-se-gestor-de-marketing-para-consultoria-otimizacao-e-implementacao-de-estrategia-de-vendas-de-cursos-on-line-de-educaca   1
https://www.workana.com/pt/job/escrever-e-mails   1
https://underdogsbiteupwards.wordpress.com/2014/12/27/job-change/?like_comment=31403&_wpnonce=f84887987a   1
https://worknowapp.com/jobs/602b6543-26df-4250-a5d5-e972903dbb25   1
https://www.worksourcewa.com/jobsearch/powersearch.aspx?q=occda&amp;rad_units=miles&amp;pp=25&amp;vw=b&amp;setype=2&amp;rad=10&amp;sort=dt.rv.di&amp;tm=30&vw=d&jbf67816=88993&jbf47538=1   1
https://www.workana.com/es/job/the-artic

https://www.worldcoffeeportal.com/5THWAVE/Podcast/2020/Championing-careers-in-the-global-coffee-industry   1
https://www.workana.com/job/court-check-criminal-and-civil-informations?ref=projects_1   1
https://www.venquis.de/job/actuarial-data-analyst-1/   1
http://workinhostels.com/latest-jobs?l=3175058&r=&c=9&sc=   1
https://www.workopolis.com/jobsearch/viewjob/VNgKpqNn0JFTaMdKCdBIVkICIOvVHlewi9B9kTZ1U0trsXo46HowCQ?ak=&l=Longueuil%2C+QC   1
https://wirsuchenphysiotherapeuten.de/jobs/pflegefachkraft-m-w-d-fuer-den-springerpol0/   1
https://worknowapp.com/jobs/10f654ef-8b11-4307-ab81-adbd686feb78   1
https://www.woller-maschinen.de/zubehor-allgemein/schweisskraft-job-manager-mega-arc-schweisskraft-1033672-zubehoer-maschinen-shop.html   1
https://www.workana.com/pt/job/iphone-e-android-app   1
https://www.valentum-kommunikation.de/agentur/vimana-auf-dem-weg-zum-traumjob-pilot/   1
https://thecareerguide.wordpress.com/category/highest-paying-jobs-in-the-u-s/   1
https://www.worknrby.com/jo

https://portal.victoria-consulting.de/job-steuerberater-m-w-d-baden-baden-2662.html?kategorie=2   1
https://www.workinsports.com/jobs/wings-stadium.asp   1
https://www.workana.com/pt/job/imagens-para-posts-em-blog-e-redes-sociais-facebook-instagran-e-linkedin   1
https://literatureismyporn.wordpress.com/2015/09/23/the-air-hostess-job/?like_comment=825&_wpnonce=cccdbc77eb   1
https://www.workana.com/pt/job/banner-para-anuncio-de-servico   1
https://www.workana.com/pt/job/artes-para-redes-sociais-feed-facebook-intagram-stories-e-artes-esporadicas   1
https://www.work-and-earn-online.com/tag/freelance-jobs/   1
https://workthenorth.com/jobs-in/georgia-atlanta/   1
https://www.workpac.com/labourer-jobs-in-Adelaide   1
https://www.workopolis.com/jobsearch/viewjob/TeBS_4rs64cLa1PZERWwS8uCraTb3t0luGUSihYjaPN4JUqPz80CMg?ak=&l=Orangeville%2C+ON   1
https://www.workopolis.com/jobsearch/loblaw-companies-limited-jobs/sarnia-ontario   1
https://www.workopolis.com/jobsearch/elk-island-school-divisio

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://www.workana.com' --fields url | wc -l

> 55

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://www.workinsports.com' --fields url | wc -l

> 1

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://seeker.worksourcewa.com' --fields url | wc -l

> 1

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://kwoted.wordpress.com' --fields url | wc -l

> 1

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://www.xn--jobbrse-stellenangebote-blc.de' --fields url | wc -l

> 5

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://www.workitdaily.com' --fields url | wc -l

> 1

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://workinhostels.com' --fields url | wc -l

> 1

cdxt --cc --from 202101 --to 202102 --filter '=status:200' iter 'https://workshift-sol.com' --fields url | wc -l

> 1